In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [4]:
pip install PyPDF2 datasets


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 5.3 MB/s eta 0:00:00a 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [1]:
!pip install transformers datasets accelerate torch


Note: you may need to restart the kernel to use updated packages.


In [6]:
!pip install numpy pandas matplotlib PyPDF2


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 4.8 MB/s eta 0:00:00a 0:00:01


In [8]:
import os
from PyPDF2 import PdfReader

# Directory containing PDF files
pdf_directory = "/kaggle/input/dataaaaaaa/works"

# Function to extract text from a PDF file
def extract_text_from_pdf(file_path):
    reader = PdfReader(file_path)
    text = ""
    for page in reader.pages:
        text += page.extract_text()  # Extract text from each page
    return text

# Loop through all PDF files in the directory
all_texts = []
for filename in os.listdir(pdf_directory):
    if filename.endswith(".pdf"):  # Ensure only PDFs are processed
        file_path = os.path.join(pdf_directory, filename)
        text = extract_text_from_pdf(file_path)
        all_texts.append(text)

print(f"Extracted text from {len(all_texts)} PDF files.")


Extracted text from 13 PDF files.


In [12]:

import re

# Combine text from all files
combined_text = " ".join(all_texts)

# Clean the combined text
cleaned_text = re.sub(r"\s+", " ", combined_text)  # Remove extra whitespace
print(cleaned_text[:500])  # Preview first 500 characters



 The Agora Foundation • www.theagorafoundation.org 1 An Honest Thief by Fyodor Dostovesky One morning, just as I was about to set off to my office, Agrafena, my cook, washerwoman and housekeeper, came in to me and, to my surprise, entered into conversation. She had always been such a silent, simple creature that, except her daily inquiry about dinner, she had not uttered a word for the last six years. I, at least, had heard nothing else from her. "Here I have come in to have a word with you, sir


In [13]:
def split_into_chunks(text, chunk_size=512):
    words = text.split()
    return [" ".join(words[i:i + chunk_size]) for i in range(0, len(words), chunk_size)]

chunks = split_into_chunks(cleaned_text)
print(f"Generated {len(chunks)} chunks.")


Generated 3404 chunks.


In [14]:
output_file = "dostoevsky_combined_text.txt"
with open(output_file, "w", encoding="utf-8") as file:
    file.write(cleaned_text)
print(f"Cleaned text saved to {output_file}.")


Cleaned text saved to dostoevsky_combined_text.txt.


In [9]:
from transformers import AutoTokenizer
from datasets import Dataset

# Load the Falcon tokenizer
model_name = "tiiuae/falcon-7b"  # Adjust model name as needed
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Prepare data for Hugging Face
data = [{"text": chunk} for chunk in chunks]  # Use the chunks created earlier
dataset = Dataset.from_list(data)

# Tokenize the dataset
def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True, max_length=512)

tokenized_dataset = dataset.map(tokenize_function, batched=True)
print("Dataset tokenized successfully!")


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Map:   0%|          | 0/3404 [00:00<?, ? examples/s]

ValueError: Asking to pad but the tokenizer does not have a padding token. Please select a token to use as `pad_token` `(tokenizer.pad_token = tokenizer.eos_token e.g.)` or add a new pad token via `tokenizer.add_special_tokens({'pad_token': '[PAD]'})`.

In [ ]:
from PyPDF2 import PdfReader

# Load the PDF file
pdf_path = "dostoevsky_works.pdf"  # Replace with your file path
reader = PdfReader(pdf_path)

# Extract text from all pages
text = ""
for page in reader.pages:
    text += page.extract_text()

print("Text extracted successfully!")


In [13]:
import re
from collections import Counter

def clean_book_text(file_path, output_path):
    """
    Clean up a book text by removing repeated phrases and numbers.
    
    Parameters:
        file_path (str): Path to the input text file.
        output_path (str): Path to save the cleaned text file.

    Returns:
        None
    """
    def remove_repeats_and_numbers(text):
        # Normalize spaces and lowercase text for consistent matching
          # Remove headers/footers

        text = re.sub(r"The Agora Foundation • www.theagorafoundation.org", " ", text).strip()
        text = re.sub(r"Chapter", " ", text).strip()
        text = re.sub(r"White Nights And Other Stories By Fyodor Dostoevsky www.globalgrey.co.uk", " ", text).strip()
        text = re.sub(r"The Third and Last Interview with Smerdyakov ", " ", text).strip()
        text = re.sub(r"\d+", "", text)  # Remove line numbers
        text = re.sub(r"\s+", " ", text).strip()  # Normalize spaces
        return text

    try:
        # Read the input file
        with open(file_path, 'r', encoding='utf-8') as file:
            original_text = file.read()

        # Clean the text
        cleaned_text = remove_repeats_and_numbers(original_text)

        # Write the cleaned text to the output file
        with open(output_path, 'w', encoding='utf-8') as file:
            file.write(cleaned_text)

        print(f"Cleaned text saved to {output_path}")
    except Exception as e:
        print(f"An error occurred: {e}")

# Example usage
if __name__ == "__main__":
    input_file = "/kaggle/input/7uirytehsrgefd/dostoevsky_combined_text (1).txt"  # Replace with the path to your input text file
    output_file = "cleaned_book.txt"  # Replace with the path to save the cleaned text
    clean_book_text(input_file, output_file)


Cleaned text saved to cleaned_book.txt


In [14]:
from collections import Counter
import re

def find_repeated_phrases(file_path, phrase_length=2):
    """
    Analyzes a text file to find repeated phrases of a given length.

    :param file_path: Path to the text file.
    :param phrase_length: Number of words in each phrase.
    :return: List of tuples with repeated phrases and their counts, ranked by frequency.
    """
    try:
        # Read the file content
        with open(file_path, 'r', encoding='utf-8') as file:
            text = file.read()

        # Normalize text: remove punctuation and convert to lowercase
        text = re.sub(r'[^a-zA-Z0-9\s]', '', text).lower()

        # Split text into words
        words = text.split()

        # Extract phrases of the specified length
        phrases = [" ".join(words[i:i + phrase_length]) for i in range(len(words) - phrase_length + 1)]

        # Count the occurrences of each phrase
        phrase_counts = Counter(phrases)

        # Filter and rank repeated phrases
        repeated_phrases = [(phrase, count) for phrase, count in phrase_counts.items() if count > 5]
        ranked_phrases = sorted(repeated_phrases, key=lambda x: x[1], reverse=True)

        return ranked_phrases

    except FileNotFoundError:
        print(f"Error: File '{file_path}' not found.")
        return []

    except Exception as e:
        print(f"An error occurred: {e}")
        return []

# Example usage
if __name__ == "__main__":
    file_path = "/kaggle/working/cleaned_book.txt"  # Replace with your text file path
    phrase_length = 9  # Specify the number of words in a phrase

    ranked_phrases = find_repeated_phrases(file_path, phrase_length)

    if ranked_phrases:
        print("Repeated phrases ranked by frequency:")
        for rank, (phrase, count) in enumerate(ranked_phrases, start=1):
            print(f"{rank}. '{phrase}' repeated {count} times")
    else:
        print("No repeated phrases found.")


Repeated phrases ranked by frequency:
1. 'the third and last intervie w with smer dyak' repeated 13 times
2. 'the galloping troika the end of the pr osecutors' repeated 9 times
3. 'galloping troika the end of the pr osecutors speec' repeated 9 times
4. 'the pr osecutors speec h sk etches of char' repeated 8 times
5. 'its always worth while speaking to a cle ver' repeated 7 times


In [ ]:
import torch
import torch.nn as nn
from torch.nn import functional as F

batch_size = 32 
block_size = 8
max_iters = 3000000
eval_interval = 300
learning_rate = 1e-3 #Could also be 1e-3, no problem with a dataset this small
device = 'cuda' if torch.cuda.is_available() else 'cpu' #Faster parallel processing if CUDA gpu is present
eval_iters = 200
n_embd = 384
n_head = 6
n_layer = 6
dropout = 0.2


with open('/kaggle/input/7uirytehsrgefd/dostoevsky_combined_text (1).txt', 'r', encoding='utf-8') as f: #Opens the lyrics file in same directory
    text = f.read()

chars = sorted(list(set(text))) #All the characters Laufey uses
vocab_size = len(chars)
stoi = { ch:i for i,ch in enumerate(chars) } #String to integer
itos = { i:ch for i,ch in enumerate(chars) } #Integer to string
encode = lambda s: [stoi[ch] for ch in s]
decode = lambda i: ''.join([itos[n] for n in i])
data = torch.tensor(encode(text), dtype = torch.long)
train_ratio = int(0.9 * len(data))
train_data = data[:train_ratio]
val_data = data[train_ratio:]

#Batch generator
def get_batch(split):
    data = train_data if split == 'train' else val_data 
    ix = torch.randint(len(data) - block_size, (batch_size,)) #Random position in text file
    x = torch.stack([data[i:i+block_size] for i in ix])
    y = torch.stack([data[i+1:i+block_size+1] for i in ix])
    x, y = x.to(device), y.to(device) #Links to cuda GPU
    return x, y

@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iters)
        for k in range(eval_iters):
            X, Y = get_batch(split)
            logits, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out


class Head(nn.Module): #Single head of final model
    def __init__(self, head_size):
        super().__init__()
        self.key = nn.Linear(n_embd, head_size, bias=False)
        self.query = nn.Linear(n_embd, head_size, bias=False)
        self.value = nn.Linear(n_embd, head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))

        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        B,T,C = x.shape
        k = self.key(x)   
        q = self.query(x) 
        wei = q @ k.transpose(-2,-1) * k.shape[-1]**-0.5 
        wei = wei.masked_fill(self.tril[:T, :T] == 0, float('-inf')) 
        wei = F.softmax(wei, dim=-1) 
        wei = self.dropout(wei)
        v = self.value(x) 
        out = wei @ v
        return out

class MultiHeadAttention(nn.Module): #Parallel processing

    def __init__(self, num_heads, head_size):
        super().__init__()
        self.heads = nn.ModuleList([Head(head_size) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, n_embd)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        out = self.dropout(self.proj(out))
        return out

class FeedFoward(nn.Module):

    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, 4 * n_embd),
            nn.ReLU(),
            nn.Linear(4 * n_embd, n_embd),
            nn.Dropout(dropout),
        )

    def forward(self, x):
        return self.net(x)

class Block(nn.Module):
    
    def __init__(self, n_embd, n_head):
        super().__init__()
        head_size = n_embd // n_head
        self.sa = MultiHeadAttention(n_head, head_size)
        self.ffwd = FeedFoward(n_embd)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)

    def forward(self, x):
        x = x + self.sa(self.ln1(x))
        x = x + self.ffwd(self.ln2(x))
        return x

class GPTLanguageModel(nn.Module):

    def __init__(self):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(n_embd, n_head=n_head) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd)
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.apply(self._init_weights)

    def _init_weights(self, module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

    def forward(self, idx, targets=None):
        B, T = idx.shape

        tok_emb = self.token_embedding_table(idx)
        pos_emb = self.position_embedding_table(torch.arange(T, device=device))
        x = tok_emb + pos_emb 
        x = self.blocks(x) 
        x = self.ln_f(x)
        logits = self.lm_head(x) 

        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B*T, C)
            targets = targets.view(B*T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]
            probs = F.softmax(logits, dim=-1) 
            idx_next = torch.multinomial(probs, num_samples=1)
            idx = torch.cat((idx, idx_next), dim=1)
        return idx

model = GPTLanguageModel()
m = model.to(device)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

optimizer = torch.optim.AdamW(model.parameters(), lr=learning_rate)

for iter in range(max_iters):

    if iter % eval_interval == 0 or iter == max_iters - 1:
        losses = estimate_loss()
        print(f"Step {iter}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")

    xb, yb = get_batch('train')

    logits, loss = model(xb, yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()

context = torch.zeros((1, 1), dtype=torch.long, device=device)
print(decode(m.generate(context, max_new_tokens=500)[0].tolist()))

10.742913 M parameters
Step 0: train loss 4.8829, val loss 4.8808
Step 300: train loss 2.4839, val loss 2.4658
Step 600: train loss 2.4311, val loss 2.4018
Step 900: train loss 2.3935, val loss 2.3880
Step 1200: train loss 2.3836, val loss 2.3641
Step 1500: train loss 2.4492, val loss 2.4214
Step 1800: train loss 2.3965, val loss 2.3780
Step 2100: train loss 2.3767, val loss 2.3693
Step 2400: train loss 2.4896, val loss 2.4674
Step 2700: train loss 2.4388, val loss 2.4393
Step 3000: train loss 2.4320, val loss 2.4060
Step 3300: train loss 2.4037, val loss 2.3963
Step 3600: train loss 2.4327, val loss 2.4164
Step 3900: train loss 2.4928, val loss 2.4935
Step 4200: train loss 2.4326, val loss 2.4113
Step 4500: train loss 2.3834, val loss 2.3785
Step 4800: train loss 2.3898, val loss 2.3667
Step 5100: train loss 2.3977, val loss 2.3803
Step 5400: train loss 2.3642, val loss 2.3633
Step 5700: train loss 2.3620, val loss 2.3536
Step 6000: train loss 2.3603, val loss 2.3816
Step 6300: train 

In [11]:
import re
import os
from sklearn.model_selection import train_test_split

# File paths
input_file = "/kaggle/input/7uirytehsrgefd/dostoevsky_combined_text (1).txt"  # Your input text file
output_dir = "processed_data"

# Create output directory
os.makedirs(output_dir, exist_ok=True)

# Load the text
with open(input_file, "r", encoding="utf-8") as file:
    text = file.read()

# Clean the text
def clean_text(text):
    # Remove headers, footers, and extra spaces
    text = re.sub(r"www.theagorafoundation.org", "", text)  # Remove headers/footers
    text = re.sub(r"\d+", "", text)  # Remove line numbers
    text = re.sub(r"\s+", " ", text).strip()  # Normalize spaces
    return text

cleaned_text = clean_text(text)
print (cleaned_text)
# Split the text into chunks (e.g., paragraphs)
chunks = cleaned_text.split("\n\n")

# Ensure we have enough chunks
if len(chunks) < 3:
    raise ValueError("Not enough data to split into train, validation, and test sets. Add more text!")

# Split into train, validation, and test sets
train_text, temp_text = train_test_split(chunks, test_size=0.2, random_state=42)
val_text, test_text = train_test_split(temp_text, test_size=0.5, random_state=42)

# Save the splits
splits = {"train": train_text, "val": val_text, "test": test_text}
for split, data in splits.items():
    with open(os.path.join(output_dir, f"{split}.txt"), "w", encoding="utf-8") as file:
        file.write("\n\n".join(data))

print("Preprocessing complete! Data saved in:", output_dir)


The Agora Foundation • An Honest Thief by Fyodor Dostovesky One morning, just as I was about to set off to my office, Agrafena, my cook, washerwoman and housekeeper, came in to me and, to my surprise, entered into conversation. She had always been such a silent, simple creature that, except her daily inquiry about dinner, she had not uttered a word for the last six years. I, at least, had heard nothing else from her. "Here I have come in to have a word with you, sir," she began abruptly; "you really ought to let the little room." "Which little room?" "Why, the one next the kitchen, to be sure." "What for?" "What for? Why because folks do take in lodgers, to be sure." "But who would take it?" "Who would take it? Why, a lodger would take it, to be sure." "But, my good woman, one could not put a bedstead in it; there wouldn't be room to move! Who could live in it?" "Who wants to live there! As long as he has a place to sleep in. Why, he would live in the window." "In what window?" "In wha

ValueError: Not enough data to split into train, validation, and test sets. Add more text!

In [5]:
import torch
import torch.nn as nn
from torch.nn import functional as F
from tqdm import tqdm
from torch.utils.tensorboard import SummaryWriter
import os

# Configuration
config = {
    'batch_size': 32,
    'block_size': 8,
    'max_iters': 3000,
    'eval_interval': 300,
    'learning_rate': 1e-3,
    'device': 'cuda' if torch.cuda.is_available() else 'cpu',
    'eval_iters': 200,
    'n_embd': 384,
    'n_head': 6,
    'n_layer': 6,
    'dropout': 0.2,
    'early_stopping_threshold': 10
}

# Prepare data
with open('/kaggle/input/sdfasdfasdfasd/LaufeyLyrics.txt', 'r', encoding='utf-8') as f:
    text = f.read()

chars = sorted(list(set(text)))
vocab_size = len(chars)
stoi = {ch: i for i, ch in enumerate(chars)}
itos = {i: ch for i, ch in enumerate(chars)}
encode = lambda s: [stoi[ch] for ch in s]
decode = lambda i: ''.join([itos[n] for n in i])
data = torch.tensor(encode(text), dtype=torch.long)
train_ratio = int(0.9 * len(data))
train_data = data[:train_ratio]
val_data = data[train_ratio:]

# Batch generator
def get_batch(split):
    data = train_data if split == 'train' else val_data
    ix = torch.randint(len(data) - config['block_size'], (config['batch_size'],))
    x = torch.stack([data[i:i + config['block_size']] for i in ix])
    y = torch.stack([data[i + 1:i + config['block_size'] + 1] for i in ix])
    return x.to(config['device']), y.to(config['device'])

@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(config['eval_iters'])
        for k in range(config['eval_iters']):
            X, Y = get_batch(split)
            _, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean().item()
    model.train()
    return out

class Head(nn.Module):
    def __init__(self, head_size):
        super().__init__()
        self.key = nn.Linear(config['n_embd'], head_size, bias=False)
        self.query = nn.Linear(config['n_embd'], head_size, bias=False)
        self.value = nn.Linear(config['n_embd'], head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(config['block_size'], config['block_size'])))
        self.dropout = nn.Dropout(config['dropout'])

    def forward(self, x):
        B, T, C = x.shape
        k = self.key(x)
        q = self.query(x)
        wei = q @ k.transpose(-2, -1) * k.shape[-1] ** -0.5
        wei = wei.masked_fill(self.tril[:T, :T] == 0, float('-inf'))
        wei = F.softmax(wei, dim=-1)
        wei = self.dropout(wei)
        v = self.value(x)
        return wei @ v

class MultiHeadAttention(nn.Module):
    def __init__(self, num_heads, head_size):
        super().__init__()
        self.heads = nn.ModuleList([Head(head_size) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, config['n_embd'])
        self.dropout = nn.Dropout(config['dropout'])

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        return self.dropout(self.proj(out))

class FeedFoward(nn.Module):
    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, 4 * n_embd),
            nn.ReLU(),
            nn.Linear(4 * n_embd, n_embd),
            nn.Dropout(config['dropout']),
        )

    def forward(self, x):
        return self.net(x)

class Block(nn.Module):
    def __init__(self, n_embd, n_head):
        super().__init__()
        head_size = n_embd // n_head
        self.sa = MultiHeadAttention(n_head, head_size)
        self.ffwd = FeedFoward(n_embd)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)

    def forward(self, x):
        x = x + self.sa(self.ln1(x))
        x = x + self.ffwd(self.ln2(x))
        return x

class GPTLanguageModel(nn.Module):
    def __init__(self):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, config['n_embd'])
        self.position_embedding_table = nn.Embedding(config['block_size'], config['n_embd'])
        self.blocks = nn.Sequential(*[Block(config['n_embd'], n_head=config['n_head']) for _ in range(config['n_layer'])])
        self.ln_f = nn.LayerNorm(config['n_embd'])
        self.lm_head = nn.Linear(config['n_embd'], vocab_size)
        self.apply(self._init_weights)

    def _init_weights(self, module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)
        pos_emb = self.position_embedding_table(torch.arange(T, device=config['device']))
        x = tok_emb + pos_emb
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)
        
        if targets is None:
            return logits, None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
            return logits, loss

    def generate(self, idx, max_new_tokens, temperature=1.0, top_k=None):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -config['block_size']:]
            logits, _ = self(idx_cond)
            logits = logits[:, -1, :] / temperature
            if top_k is not None:
                top_k_vals, _ = torch.topk(logits, top_k)
                logits[logits < top_k_vals[:, -1]] = float('-inf')
            probs = F.softmax(logits, dim=-1)
            idx_next = torch.multinomial(probs, num_samples=1)
            idx = torch.cat([idx, idx_next], dim=1)
        return idx

# Training Setup
model = GPTLanguageModel().to(config['device'])
optimizer = torch.optim.AdamW(model.parameters(), lr=config['learning_rate'])
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.5, patience=5)
writer = SummaryWriter(log_dir="./logs")

# Checkpoint Handling
checkpoint_dir = "./checkpoints"
os.makedirs(checkpoint_dir, exist_ok=True)

def save_checkpoint(model, optimizer, epoch, val_loss):
    torch.save({
        'epoch': epoch,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
        'val_loss': val_loss,
    }, os.path.join(checkpoint_dir, f"checkpoint_epoch_{epoch}.pt"))

best_val_loss = float('inf')
no_improvement_count = 0

# Training Loop
for iter in tqdm(range(config['max_iters']), desc="Training"):
    if iter % config['eval_interval'] == 0 or iter == config['max_iters'] - 1:
        losses = estimate_loss()
        train_loss = losses['train']
        val_loss = losses['val']
        print(f"Step {iter}: train loss {train_loss:.4f}, val loss {val_loss:.4f}")
        writer.add_scalar("Loss/Train", train_loss, iter)
        writer.add_scalar("Loss/Validation", val_loss, iter)

        if val_loss < best_val_loss:
            best_val_loss = val_loss
            save_checkpoint(model, optimizer, iter, val_loss)
            no_improvement_count = 0
        else:
            no_improvement_count += 1

        scheduler.step(val_loss)

        if no_improvement_count >= config['early_stopping_threshold']:
            print("Early stopping triggered.")
            break

    xb, yb = get_batch('train')
    _, loss = model(xb, yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
    optimizer.step()

# Generate Text
context = torch.zeros((1, 1), dtype=torch.long, device=config['device'])
print(decode(model.generate(context, max_new_tokens=500)[0].tolist()))
writer.close()



torch.save({"modelState": model.state_dict(), "optimizerState": optimizer.state_dict()}, "final.pth")

Training:   0%|          | 1/3000 [00:05<4:45:36,  5.71s/it]

Step 0: train loss 4.1982, val loss 4.1798


Training:  10%|▉         | 298/3000 [00:19<02:04, 21.78it/s]

Step 300: train loss 2.2622, val loss 2.2641


Training:  20%|█▉        | 598/3000 [00:39<01:49, 21.94it/s]

...

Step 2700: train loss 2.0931, val loss 2.1294


Training: 100%|█████████▉| 2998/3000 [03:17<00:00, 21.61it/s]

Step 2999: train loss 2.0780, val loss 2.1095


Training: 100%|██████████| 3000/3000 [03:23<00:00, 14.74it/s]



Ohht mn
My hik Ihaw fun momibe s I kill efed
Bat wonst

Aboune't ache hat at

Preacol


May froouwnt
Where rancee
Mad be 'sanight ghetel
Gleste ap skin
Thy
De've u tin up timeny? my be I r
Hap ine me
? sho displeshing whoot'ss wonchero kin leal fristste spey
Hown't anthen ha y that ume I sleeel

Jutet my, thist I an toning frollmeave

's knceling lett tay talle I youn Nin


Dok tat'm onigno an thero gnit
My I nono dheng dtamk
I am chart tho righseat pomeden like myow ling a my there tumame lekn 
